<a href="https://colab.research.google.com/github/hasune613/hello-world/blob/main/Optuna.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install -q optuna
import optuna

In [ ]:
!pip install -q torch

In [ ]:
import torch
import torch.nn as nn
import torch.nn.functional as F

In [ ]:
torch.cuda.get_device_name(0)

'Tesla T4'

In [ ]:
!pip install -q pytorch_lightning==1.2.4

In [ ]:
import pytorch_lightning as pl
pl.__version__

'1.2.4'

In [ ]:
!pip install -q torchmetrics
import torchmetrics

In [ ]:
def objective(trial):

    # -10 ≦ x < 10 の範囲で連続値を提案
    x = trial.suggest_uniform('x', -10, 10)

    # 目的関数を返り値に指定
    return (x - 2)**2

In [ ]:
# デフォルトで採用される TPESampler のシードを固定して再現性確保
sampler = optuna.samplers.TPESampler(seed=0)

# study オブジェクトを作成し、最適化を実行（デフォルトは最小化）
study = optuna.create_study(sampler=sampler)
study.optimize(objective, n_trials=10)

[I 2021-06-21 03:05:10,124] A new study created in memory with name: no-name-8d04606d-a1c7-443f-84ad-93df8c95a379
[I 2021-06-21 03:05:10,128] Trial 0 finished with value: 1.0480229520791995 and parameters: {'x': 0.9762700785464951}. Best is trial 0 with value: 1.0480229520791995.
[I 2021-06-21 03:05:10,130] Trial 1 finished with value: 5.307436050111796 and parameters: {'x': 4.30378732744839}. Best is trial 0 with value: 1.0480229520791995.
[I 2021-06-21 03:05:10,132] Trial 2 finished with value: 0.0030544989253336228 and parameters: {'x': 2.055267521432878}. Best is trial 2 with value: 0.0030544989253336228.
[I 2021-06-21 03:05:10,134] Trial 3 finished with value: 1.2151454066214245 and parameters: {'x': 0.8976636599379368}. Best is trial 2 with value: 0.0030544989253336228.
[I 2021-06-21 03:05:10,136] Trial 4 finished with value: 12.439051918480782 and parameters: {'x': -1.5269040132219054}. Best is trial 2 with value: 0.0030544989253336228.
[I 2021-06-21 03:05:10,139] Trial 5 finish

In [ ]:
#study.best_params

In [ ]:
from sklearn.datasets import load_breast_cancer

breast_cancer = load_breast_cancer()

x = breast_cancer['data']
t = breast_cancer['target']

x = torch.tensor(x,dtype=torch.float32)
t = torch.tensor(t,dtype=torch.int64)

dataset = torch.utils.data.TensorDataset(x,t)



In [ ]:
pl.seed_everything(0)

n_train = int(len(dataset)*0.6)
n_val = int(len(dataset)*0.2)
n_test = int(len(dataset)-n_train-n_val)

Global seed set to 0


In [ ]:
print(n_train)
print(n_val)
print(n_test)


341
113
115


In [ ]:
train,val,test = torch.utils.data.random_split(dataset,[n_train,n_val,n_test])
print(len(train))
print(len(val))
print(len(test))

341
113
115


In [ ]:

batch_size = 32
train_loader = torch.utils.data.DataLoader(train,batch_size,shuffle=True,drop_last=True)
val_loader = torch.utils.data.DataLoader(val,batch_size)
test_loader = torch.utils.data.DataLoader(test,batch_size)

In [ ]:
print(len(train_loader))
print(len(val_loader))
print(len(test_loader))

10
4
4


In [ ]:
from torchmetrics.functional import accuracy

In [ ]:
class Net(pl.LightningModule):

    # インスタンス化の際に lr を引数として指定可能に
    def __init__(self, lr=0.01):
        super().__init__()

        self.lr = lr

        self.fc1 = nn.Linear(30, 10)
        self.bn1 = nn.BatchNorm1d(10)
        self.fc2 = nn.Linear(10, 2)


    def forward(self, x):
        h = self.fc1(x)
        h = F.relu(h)
        h = self.bn1(h)
        h = self.fc2(h)
        return h


    def training_step(self, batch, batch_idx):
        x, t = batch
        y = self(x)
        loss = F.cross_entropy(y, t)
        self.log('train_loss', loss, on_step=True, on_epoch=True, prog_bar=True)
        self.log('train_acc', accuracy(y.softmax(dim=-1), t), on_step=True, on_epoch=True, prog_bar=True)
        return loss


    def validation_step(self, batch, batch_idx):
        x, t = batch
        y = self(x)
        loss = F.cross_entropy(y, t)
        self.log('val_loss', loss, on_step=False, on_epoch=True)
        self.log('val_acc', accuracy(y.softmax(dim=-1), t), on_step=False, on_epoch=True)
        return loss


    def test_step(self, batch, batch_idx):
        x, t = batch
        y = self(x)
        loss = F.cross_entropy(y, t)
        self.log('test_loss', loss, on_step=False, on_epoch=True)
        self.log('test_acc', accuracy(y.softmax(dim=-1), t), on_step=False, on_epoch=True)
        return loss


    # lr をハイパーパラメータとして最適化
    def configure_optimizers(self):
        optimizer = torch.optim.SGD(self.parameters(), lr=self.lr)
        return optimizer



In [ ]:
from pytorch_lightning.callbacks import EarlyStopping

In [ ]:
def objective(trial):

    # パラメータの候補領域
    lr = trial.suggest_loguniform('lr', 1e-5, 1e-1)

    # ネットワークの訓練（早期終了あり）
    pl.seed_everything(0)
    net = Net(lr)
    trainer = pl.Trainer(max_epochs=10, gpus=1, deterministic=True, callbacks=[EarlyStopping(monitor='val_acc')])
    trainer.fit(net, train_loader, val_loader)
    result = trainer.callback_metrics['val_acc']

    # 検証データの accuracy で評価
    return result

In [ ]:
# study オブジェクトを作成し、最適化を実行
sampler = optuna.samplers.TPESampler(seed=0)
study = optuna.create_study(sampler=sampler, direction='maximize')  # 最大化と指定
study.optimize(objective, n_trials=30)

[I 2021-06-21 03:05:10,344] A new study created in memory with name: no-name-ffdd916c-36d8-4611-aba1-395d86137618
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 310   
1 | bn1  | BatchNorm1d | 20    
2 | fc2  | Linear      | 22    
-------------------------------------
352       Trainable params
0         Non-trainable params
352       Total params
0.001     Total estimated model params size (MB)


[I 2021-06-21 03:05:12,113] Trial 0 finished with value: 0.9115044474601746 and parameters: {'lr': 0.0015676677195506068}. Best is trial 0 with value: 0.9115044474601746.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores



  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 310   
1 | bn1  | BatchNorm1d | 20    
2 | fc2  | Linear      | 22    
-------------------------------------
352       Trainable params
0         Non-trainable params
352       Total params
0.001     Total estimated model params size (MB)


[I 2021-06-21 03:05:13,990] Trial 1 finished with value: 0.9026548862457275 and parameters: {'lr': 0.007257005721594277}. Best is trial 0 with value: 0.9115044474601746.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores



  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 310   
1 | bn1  | BatchNorm1d | 20    
2 | fc2  | Linear      | 22    
-------------------------------------
352       Trainable params
0         Non-trainable params
352       Total params
0.001     Total estimated model params size (MB)


...

[I 2021-06-21 03:05:52,098] Trial 25 finished with value: 0.9115044474601746 and parameters: {'lr': 0.025516944770214534}. Best is trial 3 with value: 0.9203540086746216.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 310   
1 | bn1  | BatchNorm1d | 20    
2 | fc2  | Linear      | 22    
-------------------------------------
352       Trainable params
0         Non-trainable params
352       Total params
0.001     Total estimated model params size (MB)


[I 2021-06-21 03:05:54,238] Trial 26 finished with value: 0.9115044474601746 and parameters: {'lr': 0.003071372107508475}. Best is trial 3 with value: 0.9203540086746216.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 310   
1 | bn1  | BatchNorm1d | 20    
2 | fc2  | Linear      | 22    
-------------------------------------
352       Trainable params
0         Non-trainable params
352       Total params
0.001     Total estimated model params size (MB)


[I 2021-06-21 03:05:56,679] Trial 27 finished with value: 0.9026548862457275 and parameters: {'lr': 0.007007640024043187}. Best is trial 3 with value: 0.9203540086746216.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 310   
1 | bn1  | BatchNorm1d | 20    
2 | fc2  | Linear      | 22    
-------------------------------------
352       Trainable params
0         Non-trainable params
352       Total params
0.001     Total estimated model params size (MB)


[I 2021-06-21 03:05:57,811] Trial 28 finished with value: 0.06194690242409706 and parameters: {'lr': 0.000223519320533301}. Best is trial 3 with value: 0.9203540086746216.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 310   
1 | bn1  | BatchNorm1d | 20    
2 | fc2  | Linear      | 22    
-------------------------------------
352       Trainable params
0         Non-trainable params
352       Total params
0.001     Total estimated model params size (MB)


[I 2021-06-21 03:06:00,204] Trial 29 finished with value: 0.9115044474601746 and parameters: {'lr': 0.001532292064581655}. Best is trial 3 with value: 0.9203540086746216.


In [ ]:
# 得られた最適なパラメータ
study.best_params

{'lr': 0.0015119336467641006}

In [ ]:
# 最適なパラメータにおける目的関数の値
study.best_value

0.9203540086746216

In [ ]:
# 最も良かった試行の詳細
study.best_trial

FrozenTrial(number=3, values=[0.9203540086746216], datetime_start=datetime.datetime(2021, 6, 21, 3, 5, 15, 884805), datetime_complete=datetime.datetime(2021, 6, 21, 3, 5, 17, 797258), params={'lr': 0.0015119336467641006}, distributions={'lr': LogUniformDistribution(high=0.1, low=1e-05)}, user_attrs={}, system_attrs={}, intermediate_values={}, trial_id=3, state=TrialState.COMPLETE, value=None)

In [ ]:
# 試行結果の可視化
optuna.visualization.plot_optimization_history(study)

In [ ]:
# パラメータと目的関数の値の関係性を可視化
optuna.visualization.plot_slice(study)

In [ ]:
class Net(pl.LightningModule):

    # インスタンス化の際に lr を引数として指定可能に
    def __init__(self,n_mid=10, lr=0.01):
        super().__init__()

        self.n_mid = n_mid
        self.lr = lr

        self.fc1 = nn.Linear(30, n_mid)
        self.bn1 = nn.BatchNorm1d(n_mid)
        self.fc2 = nn.Linear(n_mid, 2)


    def forward(self, x):
        h = self.fc1(x)
        h = F.relu(h)
        h = self.bn1(h)
        h = self.fc2(h)
        return h


    def training_step(self, batch, batch_idx):
        x, t = batch
        y = self(x)
        loss = F.cross_entropy(y, t)
        self.log('train_loss', loss, on_step=True, on_epoch=True, prog_bar=True)
        self.log('train_acc', accuracy(y.softmax(dim=-1), t), on_step=True, on_epoch=True, prog_bar=True)
        return loss


    def validation_step(self, batch, batch_idx):
        x, t = batch
        y = self(x)
        loss = F.cross_entropy(y, t)
        self.log('val_loss', loss, on_step=False, on_epoch=True)
        self.log('val_acc', accuracy(y.softmax(dim=-1), t), on_step=False, on_epoch=True)
        return loss


    def test_step(self, batch, batch_idx):
        x, t = batch
        y = self(x)
        loss = F.cross_entropy(y, t)
        self.log('test_loss', loss, on_step=False, on_epoch=True)
        self.log('test_acc', accuracy(y.softmax(dim=-1), t), on_step=False, on_epoch=True)
        return loss


    # lr をハイパーパラメータとして最適化
    def configure_optimizers(self):
        optimizer = torch.optim.SGD(self.parameters(), lr=self.lr)
        return optimizer



In [ ]:
def objective(trial):

    # パラメータの候補領域
    lr = trial.suggest_loguniform('lr', 1e-5, 1e-1)
    n_mid = trial.suggest_int('n_mid',2,100)

    # ネットワークの訓練（早期終了あり）
    pl.seed_everything(0)
    net = Net(n_mid,lr)
    trainer = pl.Trainer(max_epochs=10, gpus=1, deterministic=True, callbacks=[EarlyStopping(monitor='val_acc')])
    trainer.fit(net, train_loader, val_loader)
    result = trainer.callback_metrics['val_acc']

    # 検証データの accuracy で評価
    return result

In [ ]:
# study オブジェクトを作成し、最適化を実行
sampler = optuna.samplers.TPESampler(seed=0)
study = optuna.create_study(sampler=sampler, direction='maximize')  # 最大化と指定
study.optimize(objective, n_trials=30)

[I 2021-06-21 03:06:00,871] A new study created in memory with name: no-name-9d37452d-bb8d-442b-8d75-ad310d72c4e3
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 2.2 K 
1 | bn1  | BatchNorm1d | 144   
2 | fc2  | Linear      | 146   
-------------------------------------
2.5 K     Trainable params
0         Non-trainable params
2.5 K     Total params
0.010     Total estimated model params size (MB)


[I 2021-06-21 03:06:03,240] Trial 0 finished with value: 0.9115044474601746 and parameters: {'lr': 0.0015676677195506068, 'n_mid': 72}. Best is trial 0 with value: 0.9115044474601746.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 1.7 K 
1 | bn1  | BatchNorm1d | 110   
2 | fc2  | Linear      | 112   
-------------------------------------
1.9 K     Trainable params
0         Non-trainable params
1.9 K     Total params
0.008     Total estimated model params size (MB)


[I 2021-06-21 03:06:05,024] Trial 1 finished with value: 0.9115044474601746 and parameters: {'lr': 0.0025766385746135885, 'n_mid': 55}. Best is trial 0 with value: 0.9115044474601746.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 2.0 K 
1 | bn1  | BatchNorm1d | 130   
2 | fc2  | Linear      | 132   
-------------------------------------
2.3 K     Trainable params
0         Non-trainable params
2.3 K     Total params
0.009     Total estimated model params size (MB)


[I 2021-06-21 03:06:07,639] Trial 2 finished with value: 0.9203540086746216 and parameters: {'lr': 0.0004950159553733195, 'n_mid': 65}. Best is trial 2 with value: 0.9203540086746216.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 2.8 K 
1 | bn1  | BatchNorm1d | 180   
2 | fc2  | Linear      | 182   
-------------------------------------
3.2 K     Trainable params
0         Non-trainable params
3.2 K     Total params
0.013     Total estimated model params size (MB)


[I 2021-06-21 03:06:09,587] Trial 3 finished with value: 0.9115044474601746 and parameters: {'lr': 0.0005627932047415167, 'n_mid': 90}. Best is trial 2 with value: 0.9203540086746216.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 1.2 K 
1 | bn1  | BatchNorm1d | 78    
2 | fc2  | Linear      | 80    
-------------------------------------
1.4 K     Trainable params
0         Non-trainable params
1.4 K     Total params
0.005     Total estimated model params size (MB)


...

[I 2021-06-21 03:06:48,953] Trial 25 finished with value: 0.9115044474601746 and parameters: {'lr': 0.0009983916988840077, 'n_mid': 34}. Best is trial 6 with value: 0.9380530714988708.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 2.9 K 
1 | bn1  | BatchNorm1d | 184   
2 | fc2  | Linear      | 186   
-------------------------------------
3.2 K     Trainable params
0         Non-trainable params
3.2 K     Total params
0.013     Total estimated model params size (MB)


[I 2021-06-21 03:06:50,864] Trial 26 finished with value: 0.9203540086746216 and parameters: {'lr': 0.0019527432298457885, 'n_mid': 92}. Best is trial 6 with value: 0.9380530714988708.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 1.4 K 
1 | bn1  | BatchNorm1d | 88    
2 | fc2  | Linear      | 90    
-------------------------------------
1.5 K     Trainable params
0         Non-trainable params
1.5 K     Total params
0.006     Total estimated model params size (MB)


[I 2021-06-21 03:06:52,874] Trial 27 finished with value: 0.76106196641922 and parameters: {'lr': 2.677722712910656e-05, 'n_mid': 44}. Best is trial 6 with value: 0.9380530714988708.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 2.1 K 
1 | bn1  | BatchNorm1d | 138   
2 | fc2  | Linear      | 140   
-------------------------------------
2.4 K     Trainable params
0         Non-trainable params
2.4 K     Total params
0.010     Total estimated model params size (MB)


[I 2021-06-21 03:06:53,999] Trial 28 finished with value: 0.0796460211277008 and parameters: {'lr': 0.00026485990985802274, 'n_mid': 69}. Best is trial 6 with value: 0.9380530714988708.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name | Type        | Params
-------------------------------------
0 | fc1  | Linear      | 2.5 K 
1 | bn1  | BatchNorm1d | 160   
2 | fc2  | Linear      | 162   
-------------------------------------
2.8 K     Trainable params
0         Non-trainable params
2.8 K     Total params
0.011     Total estimated model params size (MB)


[I 2021-06-21 03:06:55,672] Trial 29 finished with value: 0.9292035102844238 and parameters: {'lr': 0.0340876668801366, 'n_mid': 80}. Best is trial 6 with value: 0.9380530714988708.


In [ ]:
# 得られた最適なパラメータの組み合わせ
study.best_params

{'lr': 0.001871450068624067, 'n_mid': 93}

In [ ]:
# 最適なパラメータの組み合わせにおける目的関数の値
study.best_value

0.9380530714988708

In [ ]:
# 試行結果の可視化
# optuna.visualization.plot_optimization_history(study)

In [ ]:
# 2 つのパラメータの関係性を等高線でプロット
# optuna.visualization.plot_contour(study)

In [ ]:
layers = nn.Sequential()
layers

Sequential()

In [ ]:
for n in range(3):
    layers.add_module(f'fc{n+1}',nn.Linear(30,30))
    layers.add_module(f'act{n+1}',nn.ReLU())
    layers.add_module(f'bn{n+1}',nn.BatchNorm1d(30))


In [ ]:
layers

Sequential(
  (fc1): Linear(in_features=30, out_features=30, bias=True)
  (act1): ReLU()
  (bn1): BatchNorm1d(30, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (fc2): Linear(in_features=30, out_features=30, bias=True)
  (act2): ReLU()
  (bn2): BatchNorm1d(30, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (fc3): Linear(in_features=30, out_features=30, bias=True)
  (act3): ReLU()
  (bn3): BatchNorm1d(30, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
)

In [ ]:
class Net(pl.LightningModule):

    def __init__(self,n_layers=1,n_mid=10,lr=0.01):
        super().__init__()

        self.n_layers = n_layers
        self.n_mid = n_mid
        self.lr = lr

        self.layers = nn.Sequential()
        for n in range(self.n_layers):
            if n == 0:
                self.layers.add_module(f'fc{n+1}',nn.Linear(30,self.n_mid))
            else:
                self.layers.add_module(f'fc{n+1}',nn.Linear(self.n_mid,self.n_mid))
            self.layers.add_module(f'act{n+1}',nn.ReLU())
            self.layers.add_module(f'bn{n+1}',nn.BatchNorm1d(self.n_mid))
        
        self.layers.add_module(f'fc{self.n_layers+1}',nn.Linear(self.n_mid,2))

    def forward(self,x):
        h = self.layers(x)
        return h

    def training_step(self,batch,batch_idx):
        x , t = batch
        y = self(x)
        loss = F.cross_entropy(y,t)
        self.log('train_loss',loss,on_step=True,on_epoch=True,prog_bar=True)
        self.log('train_acc',accuracy(y.softmax(dim=-1),t),on_step=True,on_epoch=True,prog_bar=True)
        return loss

    def validation_step(self,batch,batch_idx):
        x , t = batch
        y = self(x)
        loss = F.cross_entropy(y,t)
        self.log('val_log',loss,on_step=False,on_epoch=True)
        self.log('val_acc',accuracy(y.softmax(dim=-1),t),on_step=False,on_epoch=True)
        return loss
    
    def test_step(self,batch,batch_idx):
        x , t = batch
        y = self(x)
        loss = F.cross_entropy(y,t)
        self.log('test_log',loss,on_step=False,on_epoch=True)
        self.log('test_acc',accuracy(y.softmax(dim=-1),t),on_step=False,on_epoch=True)
        return loss

    def configure_optimizers(self):
        optimizer = torch.optim.SGD(self.parameters(),lr=self.lr)
        return optimizer

In [ ]:
net = Net(n_layers=1)
net

Net(
  (layers): Sequential(
    (fc1): Linear(in_features=30, out_features=10, bias=True)
    (act1): ReLU()
    (bn1): BatchNorm1d(10, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (fc2): Linear(in_features=10, out_features=2, bias=True)
  )
)

In [ ]:
net = Net(n_layers=5)
net

Net(
  (layers): Sequential(
    (fc1): Linear(in_features=30, out_features=10, bias=True)
    (act1): ReLU()
    (bn1): BatchNorm1d(10, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (fc2): Linear(in_features=10, out_features=10, bias=True)
    (act2): ReLU()
    (bn2): BatchNorm1d(10, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (fc3): Linear(in_features=10, out_features=10, bias=True)
    (act3): ReLU()
    (bn3): BatchNorm1d(10, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (fc4): Linear(in_features=10, out_features=10, bias=True)
    (act4): ReLU()
    (bn4): BatchNorm1d(10, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (fc5): Linear(in_features=10, out_features=10, bias=True)
    (act5): ReLU()
    (bn5): BatchNorm1d(10, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    (fc6): Linear(in_features=10, out_features=2, bias=True)
  )
)

In [ ]:
from pytorch_lightning.callbacks import EarlyStopping

In [ ]:
def objective(trial):

    # パラメータの候補領域
    n_layers = trial.suggest_int('n_layers', 1, 5)
    n_mid = trial.suggest_int('n_mid', 2, 100)
    lr = trial.suggest_loguniform('lr', 1e-5, 1e-1)

    # ネットワークの訓練（早期終了あり）
    pl.seed_everything(0)
    net = Net(n_layers, n_mid, lr)
    trainer = pl.Trainer(max_epochs=10, gpus=1, deterministic=True, callbacks=[EarlyStopping(monitor='val_acc')])
    trainer.fit(net, train_loader, val_loader)
    result = trainer.callback_metrics['val_acc']

    # 検証データの accuracy で評価
    return result

In [ ]:
# study オブジェクトを作成し、最適化を実行
sampler = optuna.samplers.TPESampler(seed=0)
study = optuna.create_study(sampler=sampler, direction='maximize')  # 最大化と指定
study.optimize(objective, n_trials=30)

[I 2021-06-21 03:06:56,499] A new study created in memory with name: no-name-15325699-16fc-44a3-a24a-06248b61f446
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name   | Type       | Params
--------------------------------------
0 | layers | Sequential | 13.3 K
--------------------------------------
13.3 K    Trainable params
0         Non-trainable params
13.3 K    Total params
0.053     Total estimated model params size (MB)


[I 2021-06-21 03:06:57,628] Trial 0 finished with value: 0.9203540086746216 and parameters: {'n_layers': 3, 'n_mid': 72, 'lr': 0.0025766385746135885}. Best is trial 0 with value: 0.9203540086746216.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name   | Type       | Params
--------------------------------------
0 | layers | Sequential | 5.5 K 
--------------------------------------
5.5 K     Trainable params
0         Non-trainable params
5.5 K     Total params
0.022     Total estimated model params size (MB)


[I 2021-06-21 03:06:59,692] Trial 1 finished with value: 0.6725663542747498 and parameters: {'n_layers': 3, 'n_mid': 43, 'lr': 0.0038333321561566623}. Best is trial 0 with value: 0.9203540086746216.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name   | Type       | Params
--------------------------------------
0 | layers | Sequential | 19.9 K
--------------------------------------
19.9 K    Trainable params
0         Non-trainable params
19.9 K    Total params
0.080     Total estimated model params size (MB)


[I 2021-06-21 03:07:01,064] Trial 2 finished with value: 0.8407079577445984 and parameters: {'n_layers': 3, 'n_mid': 90, 'lr': 0.07155682161754869}. Best is trial 0 with value: 0.9203540086746216.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name   | Type       | Params
--------------------------------------
0 | layers | Sequential | 9.4 K 
--------------------------------------
9.4 K     Trainable params
0         Non-trainable params
9.4 K     Total params
0.038     Total estimated model params size (MB)


[I 2021-06-21 03:07:03,624] Trial 3 finished with value: 0.9115044474601746 and parameters: {'n_layers': 2, 'n_mid': 80, 'lr': 0.001304907355036239}. Best is trial 0 with value: 0.9203540086746216.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name   | Type       | Params
--------------------------------------
0 | layers | Sequential | 21.1 K
--------------------------------------
21.1 K    Trainable params
0         Non-trainable params
21.1 K    Total params
0.084     Total estimated model params size (MB)


...

[I 2021-06-21 03:07:41,742] Trial 25 finished with value: 0.9026548862457275 and parameters: {'n_layers': 2, 'n_mid': 75, 'lr': 0.008144781102550668}. Best is trial 15 with value: 0.9292035102844238.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name   | Type       | Params
--------------------------------------
0 | layers | Sequential | 1.3 K 
--------------------------------------
1.3 K     Trainable params
0         Non-trainable params
1.3 K     Total params
0.005     Total estimated model params size (MB)


[I 2021-06-21 03:07:44,223] Trial 26 finished with value: 0.8672566413879395 and parameters: {'n_layers': 1, 'n_mid': 37, 'lr': 0.0007244099853895827}. Best is trial 15 with value: 0.9292035102844238.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name   | Type       | Params
--------------------------------------
0 | layers | Sequential | 10.9 K
--------------------------------------
10.9 K    Trainable params
0         Non-trainable params
10.9 K    Total params
0.044     Total estimated model params size (MB)


[I 2021-06-21 03:07:46,704] Trial 27 finished with value: 0.8053097128868103 and parameters: {'n_layers': 2, 'n_mid': 87, 'lr': 0.00021321151014771063}. Best is trial 15 with value: 0.9292035102844238.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name   | Type       | Params
--------------------------------------
0 | layers | Sequential | 12.6 K
--------------------------------------
12.6 K    Trainable params
0         Non-trainable params
12.6 K    Total params
0.051     Total estimated model params size (MB)


[I 2021-06-21 03:07:48,510] Trial 28 finished with value: 0.9292035102844238 and parameters: {'n_layers': 2, 'n_mid': 95, 'lr': 0.021790642520392717}. Best is trial 15 with value: 0.9292035102844238.
Global seed set to 0
GPU available: True, used: True
TPU available: None, using: 0 TPU cores

  | Name   | Type       | Params
--------------------------------------
0 | layers | Sequential | 12.0 K
--------------------------------------
12.0 K    Trainable params
0         Non-trainable params
12.0 K    Total params
0.048     Total estimated model params size (MB)


[I 2021-06-21 03:07:50,779] Trial 29 finished with value: 0.9292035102844238 and parameters: {'n_layers': 3, 'n_mid': 68, 'lr': 0.001969497610559843}. Best is trial 15 with value: 0.9292035102844238.


In [ ]:
study.best_params

{'lr': 0.0039364709713829195, 'n_layers': 2, 'n_mid': 100}

In [ ]:
study.best_value

0.9292035102844238

In [ ]:
optuna.visualization.plot_optimization_history(study)

In [ ]:
optuna.visualization.plot_contour(study)

In [ ]:
import numpy as np

x = np.array([1,2,3])
for i in x:
    print ((i**2+3*i+2).sum())




6
12
20
